In [65]:
import pandas as pd
import numpy as np

import folium
from folium import plugins

In [66]:
covid = pd.read_csv('Dados-covid-19-municipios.csv', sep =';')
cidades = pd.read_csv('https://raw.githubusercontent.com/sandeco/CanalSandeco/master/covid-19/cidades_brasil.csv')

### Adapt
The data frame "covid" is a csv file with IBGE code(unique to each city), name of the city, number of cases and deaths by Covid-19. To apply the data to a map we need the coordinates of this places, for that we used "cidades" which contain IBGE code, name of the city and coordinates.

In [67]:
covid.head()

Cod_IBGE Grande regi�o         Munic�pio  Mun_Total de casos  \
0  3500105.0      Interior        Adamantina              3817.0   
1  3500204.0      Interior            Adolfo               622.0   
2  3500303.0      Interior             Agua�              3603.0   
3  3500402.0      Interior    �guas da Prata               653.0   
4  3500501.0      Interior  �guas de Lind�ia              2055.0   

   Mun_Total de �bitos  Unnamed: 5  Unnamed: 6  Unnamed: 7  
0                134.0         NaN         NaN         NaN  
1                 19.0         NaN         NaN         NaN  
2                111.0         NaN         NaN         NaN  
3                 27.0         NaN         NaN         NaN  
4                 51.0         NaN         NaN         NaN

In [68]:
cidades.head()

codigo_ibge                 nome  latitude  longitude  capital  codigo_uf
0      5200050      Abadia de Goiás -16.75730   -49.4412        0         52
1      3100104  Abadia dos Dourados -18.48310   -47.3916        0         31
2      5200100            Abadiânia -16.19700   -48.7057        0         52
3      3100203               Abaeté -19.15510   -45.4444        0         31
4      1500107           Abaetetuba  -1.72183   -48.8788        0         15

In [69]:
covid['Cod_IBGE'] = pd.to_numeric(covid['Cod_IBGE'],downcast='integer', errors = 'coerce')
cidades['codigo_ibge'] = pd.to_numeric(cidades['codigo_ibge'],downcast='float', errors = 'coerce')

In [70]:
cidades = cidades.set_index('codigo_ibge')

In [71]:
covid = covid.rename({'Cod_IBGE': 'codigo_ibge'}, axis=1) 

### Join
The next step is to merge both dataframes, at the end we want a single dataframe with IBGE code, coordinates, name of the city, cases and deaths by Covid-19.

In [72]:
cidades = pd.merge(cidades, covid, on="codigo_ibge")

In [73]:
cidades.head()

codigo_ibge              nome  latitude  longitude  capital  codigo_uf  \
0    3500105.0        Adamantina  -21.6820   -51.0737        0         35   
1    3500204.0            Adolfo  -21.2325   -49.6451        0         35   
2    3500303.0             Aguaí  -22.0572   -46.9735        0         35   
3    3500402.0    Águas da Prata  -21.9319   -46.7176        0         35   
4    3500501.0  Águas de Lindóia  -22.4733   -46.6314        0         35   

  Grande regi�o         Munic�pio  Mun_Total de casos  Mun_Total de �bitos  \
0      Interior        Adamantina              3817.0                134.0   
1      Interior            Adolfo               622.0                 19.0   
2      Interior             Agua�              3603.0                111.0   
3      Interior    �guas da Prata               653.0                 27.0   
4      Interior  �guas de Lind�ia              2055.0                 51.0   

   Unnamed: 5  Unnamed: 6  Unnamed: 7  
0         NaN         NaN         NaN  
1         NaN         NaN         NaN  
2         NaN         NaN         NaN  
3         NaN         NaN         NaN  
4         NaN         NaN         NaN

In [74]:
cidades = cidades.drop(["Unnamed: 5","Unnamed: 6","Unnamed: 7","capital","Grande regi�o","Munic�pio","codigo_uf"], axis = 1)

In [75]:
cidades.head()

codigo_ibge              nome  latitude  longitude  Mun_Total de casos  \
0    3500105.0        Adamantina  -21.6820   -51.0737              3817.0   
1    3500204.0            Adolfo  -21.2325   -49.6451               622.0   
2    3500303.0             Aguaí  -22.0572   -46.9735              3603.0   
3    3500402.0    Águas da Prata  -21.9319   -46.7176               653.0   
4    3500501.0  Águas de Lindóia  -22.4733   -46.6314              2055.0   

   Mun_Total de �bitos  
0                134.0  
1                 19.0  
2                111.0  
3                 27.0  
4                 51.0

In [76]:
cidades["nome"]

0                Adamantina
1                    Adolfo
2                     Aguaí
3            Águas da Prata
4          Águas de Lindóia
               ...         
640    Vista Alegre do Alto
641          Vitória Brasil
642              Votorantim
643             Votuporanga
644                Zacarias
Name: nome, Length: 645, dtype: object

### Map
To display the data, first we need a base map, which is in "mapa". On our base map made with folium is centered in São Paulo - Brazil. We'll also need a json file with the shape of each city in state of São Paulo.
The shape file used is missing the fallowing cities: Mogi Mirim, Embu das Artes e São Luiz do Paraitinga.

In [77]:
mapa = folium.Map( 
    width = "100%", #Here we can choose the size of our map, 
    height = "100%", #100% mean it will cover 100% of the screen (any size).
    location = [-23.36, -46.84], #SP
    zoom_start = 7
)

In [78]:
mapa

In [79]:
import json
import requests 
r = requests.get('https://raw.githubusercontent.com/tbrugz/geodata-br/master/geojson/geojs-35-mun.json')
geo_json_data = r.json()
print(geo_json_data)

{'type': 'FeatureCollection', 'features': [{'type': 'Feature', 'properties': {'id': '3500105', 'name': 'Adamantina', 'description': 'Adamantina'}, 'geometry': {'type': 'Polygon', 'coordinates': [[[-51.0578686748, -21.3988835488], [-51.0536454977, -21.4046228386], [-51.0450043489, -21.4037238276], [-51.045439432, -21.4063589008], [-51.0397224364, -21.4067760488], [-51.0330880762, -21.408863112], [-51.0247100808, -21.4208663742], [-51.0245845013, -21.4263462599], [-51.0033347502, -21.4385388237], [-50.9925874583, -21.4367999015], [-50.9911744426, -21.4418090183], [-50.9772464698, -21.4526305135], [-50.9674002039, -21.4750044331], [-50.9701364325, -21.4791879543], [-50.9651317696, -21.4838230857], [-50.9672264355, -21.4912547321], [-50.9644621647, -21.5045943621], [-50.9684617375, -21.5150857178], [-50.9639572448, -21.5215964229], [-50.9656099653, -21.5382668569], [-50.96736118, -21.5431056598], [-50.9739312904, -21.5459116694], [-50.9748171251, -21.5613375835], [-50.9712131933, -21.56859

In [80]:
#The IBGE code in "geo_json_data" is a string, but in "cidades" is a float. So, we need to convert it.
cidades['codigo_ibge'] = cidades['codigo_ibge'].apply(int)
cidades['codigo_ibge'] = cidades['codigo_ibge'].apply(str)

## Logarithmic scale
Our data has a wide range of values, so the Logarithmic scale is a good choice yo display information more easily. 

In [81]:
#
cidades["log_casos"] = np.log(cidades["Mun_Total de casos"]+1) #add +1, because if there is no case it will return a error
cidades["log_mortes"] = np.log(cidades["Mun_Total de �bitos"]+1)

In [82]:
cidades.head()

codigo_ibge              nome  latitude  longitude  Mun_Total de casos  \
0     3500105        Adamantina  -21.6820   -51.0737              3817.0   
1     3500204            Adolfo  -21.2325   -49.6451               622.0   
2     3500303             Aguaí  -22.0572   -46.9735              3603.0   
3     3500402    Águas da Prata  -21.9319   -46.7176               653.0   
4     3500501  Águas de Lindóia  -22.4733   -46.6314              2055.0   

   Mun_Total de �bitos  log_casos  log_mortes  
0                134.0   8.247482    4.905275  
1                 19.0   6.434547    2.995732  
2                111.0   8.189800    4.718499  
3                 27.0   6.483107    3.332205  
4                 51.0   7.628518    3.951244

In [83]:
#This step is optional, it is a theme color for our base map.
folium.TileLayer('cartodbdark_matter').add_to(mapa)

In [84]:
folium.Choropleth(
    geo_data = geo_json_data,
    name = "Casos",
    data = cidades,
    columns = ["nome", "log_casos",],
    key_on = "feature.properties.name",
    fill_color = "Reds",
    fill_opacity = 0.5,
    line_color = "black",
    line_opacity = 0.6,
    show = False,
    legend_name = "Log de casos de Covid-19 em São Paulo"
    #Cores: Reds, BuGn, BuPu, GnBu, OrRd, PuBu, PuBuGn, PuRd, RdPu, YlGn, YlGnBu ...
).add_to(mapa)

In [85]:
geo_json_data['features'][0]['properties']['id']

'3500105'

In [86]:
mapa

In [87]:
cidades["Mun_Total de casos"][cidades["nome"] == "São Luiz do Paraitinga"]
### Os municipios de Mogi mirim, Embu das artes e São Luiz do Paraitinga não estão no arquivo Json

561    946.0
Name: Mun_Total de casos, dtype: float64

In [88]:
folium.Choropleth(
    geo_data = geo_json_data,
    name = "mortes",
    data = cidades,
    columns = ["nome", "log_mortes"],
    key_on = "feature.properties.name",
    fill_color = "BuGn",
    fill_opacity = 0.7,
    line_color = "black",
    line_opacity = 0.6,
    show = False,
    legend_name = "Log de mortes de Covid-19 em São Paulo"
    #Cores: Reds, BuGn, BuPu, GnBu, OrRd, PuBu, PuBuGn, PuRd, RdPu, YlGn, YlGnBu ...
).add_to(mapa)

In [89]:
cidades.head()

codigo_ibge              nome  latitude  longitude  Mun_Total de casos  \
0     3500105        Adamantina  -21.6820   -51.0737              3817.0   
1     3500204            Adolfo  -21.2325   -49.6451               622.0   
2     3500303             Aguaí  -22.0572   -46.9735              3603.0   
3     3500402    Águas da Prata  -21.9319   -46.7176               653.0   
4     3500501  Águas de Lindóia  -22.4733   -46.6314              2055.0   

   Mun_Total de �bitos  log_casos  log_mortes  
0                134.0   8.247482    4.905275  
1                 19.0   6.434547    2.995732  
2                111.0   8.189800    4.718499  
3                 27.0   6.483107    3.332205  
4                 51.0   7.628518    3.951244

### Heat Map

In [90]:
coordenadas = cidades[["latitude","longitude","Mun_Total de casos"]]

In [91]:
mapa = mapa.add_child(plugins.HeatMap(coordenadas))

In [92]:
folium.LayerControl().add_to(mapa)

In [93]:
mapa.save('index.html')